# Overview
This project explores Aspect Based Sentiment Analysis from MyAnimeList for anime reviews.

This project consists of three main parts. First, we scrap the reviews. Second, me model the sentiment analysis. Third, we present the sorted anime rankings using the outputs of the sentiment analysis.

# Webscraper

In [41]:
from urllib.request import urlopen
from bs4 import BeautifulSoup
import time

from anime_absa import get_overall_review_sentiment

reviews = []
for page in range(1,7): # TODO Make this page limit dynamic
    url = f"https://myanimelist.net/anime/32686/Keijo/reviews?sort=suggested&filter_check=&filter_hide=&preliminary=on&spoiler=off&p={page}"
    page = urlopen(url)
    html_bytes = page.read()
    html = html_bytes.decode("utf-8")
    soup = BeautifulSoup(html)
    reviews.extend(soup.find_all("div", attrs={"class": "review-element js-review-element"}))
    for review in reviews:
        print(review.prettify())
    time.sleep(0.5)

<div class="review-element js-review-element" data-reactions='{"icon":["1","7","3"],"num":860,"count":["788","10","25","1","2","8","26"]}'>
 <div class="thumbbody mt8">
  <div class="thumb">
   <a class="ga-click" data-ga-click-type="review-anime-reviewer-pic" href="https://myanimelist.net/profile/HaXXspetten">
    <img class="lazyloaded" data-src="https://cdn.myanimelist.net/s/common/userimages/3777efdb-fb89-494f-a6f8-00ddc72a1f85_42x62_i?s=48801dbeb313e3174d9029344f34e932" src="https://cdn.myanimelist.net/s/common/userimages/3777efdb-fb89-494f-a6f8-00ddc72a1f85_42x62_i?s=48801dbeb313e3174d9029344f34e932" width="48"/>
   </a>
  </div>
  <div class="body">
   <div class="update_at" title="2:21 PM">
    Dec 22, 2016
   </div>
   <div class="username">
    <a class="ga-click" data-ga-click-type="review-anime-reviewer" href="https://myanimelist.net/profile/HaXXspetten">
     HaXXspetten
    </a>
   </div>
   <div class="tags">
    <div class="tag recommended btn-label js-btn-label" data-h

In [42]:
clean_reviews = []
for review in reviews:
    # TODO: Might need to filter by class before removing spans to handle short reviews.
    recommend = review.find("div", class_= "tag").get_text()

    review_text = review.find("div", attrs={"class": "text"})
    
    if review_text.span is not None:
        
        review_text.span.extract()
        extended_review = review_text.span.extract().get_text()
        clean_reviews.append((recommend,review_text.get_text() + extended_review))
for clean_review in clean_reviews:
    print(clean_review)
    print("--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------")


('Recommended', '\n                If you ever have worshipped an ass\r\nYou would know it\'s a feminine mass\r\nBut did you ever know\r\nThat it\'s not just for show\r\nThere is more to it than just its class\n\r\nSee, the butt can be used as a tool\r\nAs a weapon to wield in a school\r\nWhere they learn the skill tree\r\nKnown as asstronomy\n\n\nAnd are taught how to use it to duel\n\r\nBut let us not forget \'bout the breasts\r\nYou know, those lovely mounds on girls\' chests\r\nAs I\'m sure you can tell\r\nThey can use those as well\r\nTo surpass all different kinds of tests\n\r\nSo these ultimate weapons of war\r\nThey will clash like never seen before\r\nAnd the last girl to stand\r\nRemaining on the Land\r\nWill make the audience beg for more\n\n\r\nYes indeed, Keijo is truly an asstounding anime in its own right. Japan just never ceases to amaze me.\n\r\nThe concept of having an anime about a highly oversexualized fictional wrestling sport for girls where they can only use thei

In [43]:
print(len(clean_reviews))

117


# Transformers Built-in Sentiment Analysis
This is using the Transformers built-in sentiment analysis. #TODO Swap out this sentiment analysis system with absa and see if this does a better job with the reviewer.

In [44]:
import torch
from transformers import pipeline, is_torch_available
print(torch.__version__)
print(is_torch_available())
sentiment_pipeline = pipeline("sentiment-analysis")

data = [clean_reviews[0][1][:300]]
sentiment_pipeline(data)

No model was supplied, defaulted to distilbert/distilbert-base-uncased-finetuned-sst-2-english and revision 714eb0f (https://huggingface.co/distilbert/distilbert-base-uncased-finetuned-sst-2-english).
Using a pipeline without specifying a model name and revision in production is not recommended.
Device set to use mps:0


2.6.0
True


[{'label': 'NEGATIVE', 'score': 0.5053225755691528}]

In [45]:
data = [clean_reviews[6][1][:300]]
sentiment_pipeline(data)

[{'label': 'POSITIVE', 'score': 0.9826387166976929}]

In [46]:
data = [review[1][:300] for review in clean_reviews]
review_sentiments = sentiment_pipeline(data)

In [47]:
print(clean_reviews[1][0])

Recommended


In [48]:
accuracy_list = []
correct_guesses, wrong_guesses = 0,0
for i in range(len(review_sentiments)):
    if (review_sentiments[i]["label"] == "POSITIVE" and clean_reviews[i][0] == "Recommended") or (review_sentiments[i]["label"] == "NEGATIVE" and clean_reviews[i][0] == "Not Recommended"):
        correct_guesses +=1
    else:
        wrong_guesses +=1
    accuracy_list.append((review_sentiments[i]["label"], clean_reviews[i][0]))

print(f"The correct guesses are: {correct_guesses} and the wrong guesses are: {wrong_guesses}")

The correct guesses are: 56 and the wrong guesses are: 61


# ABSA sentiment


In [ ]:
import json
data = [review[1][-512:] for review in clean_reviews]
#absa_review_sentiments = [get_overall_review_sentiment(text) for text in data]
absa_review_sentiments = []
noaspectterm_list = []
aspect_reviews = []
for text in data:
    sentiment = get_overall_review_sentiment(text)
    absa_review_sentiments.append(sentiment)
    if sentiment is None:
        noaspectterm_list.append(text)
    else:
        aspect_reviews.append(text)

json_noaspect_reviews = json.dumps(noaspectterm_list, indent=4)
with open('noaspectterm_reviews.json','w') as f:
    f.write(json_noaspect_reviews)

json_aspect_reviews = json.dumps(aspect_reviews, indent=4)
with open('aspectterm_reviews.json','w') as f:
    f.write(json_aspect_reviews)

Extraction Model output blah:  animation quality, action, scenes
Sentiment Model output:  negative
Sentiment Model output:  positive
Sentiment Model output:  positive
noaspectterm found
noaspectterm found
noaspectterm found
Extraction Model output blah:  sound design, sound design, combat, sound
Sentiment Model output:  none
Sentiment Model output:  none
Sentiment Model output:  none
Sentiment Model output:  none
Extraction Model output blah:  characters, premise, premise
Sentiment Model output:  positive
Sentiment Model output:  conflict
Sentiment Model output:  conflict
noaspectterm found
noaspectterm found
Extraction Model output blah:  artwork, tits, ass
Sentiment Model output:  negative
Sentiment Model output:  neutral
Sentiment Model output:  none
Extraction Model output blah:  plot armour, jokes
Sentiment Model output:  none
Sentiment Model output:  negative
Extraction Model output blah:  visuals, action, comedy
Sentiment Model output:  none
Sentiment Model output:  positive
Sen

In [31]:
accuracy_list = []
reviews_with_ratings = []
true_pos, true_neg, false_pos, false_neg, = 0,0,0,0
for i in range(len(absa_review_sentiments)):
    if absa_review_sentiments[i] is not None:
        reviews_with_ratings.append({
            "prediction" : absa_review_sentiments[i],
            "actual" : clean_reviews[i][0],
            "text" : data[i]
        })
        if (absa_review_sentiments[i] > 0.5 and clean_reviews[i][0] == "Recommended"):
            true_pos += 1
        elif (absa_review_sentiments[i] <= 0.5 and clean_reviews[i][0] == "Not Recommended"):
            true_neg +=1
        elif (absa_review_sentiments[i] <= 0.5 and clean_reviews[i][0] == "Recommended"):
            false_neg +=1
        elif (absa_review_sentiments[i] > 0.5 and clean_reviews[i][0] == "Not Recommended"):
            false_pos +=1
    #accuracy_list.append((absa_review_sentiments[i]["label"], clean_reviews[i][0]))

json_reviews = json.dumps(reviews_with_ratings, indent=4)
with open('json_reviews.json','w') as f:
    f.write(json_reviews)

print(f"The correct guesses are: {true_pos + true_neg} and the wrong guesses are: {false_pos + false_neg}.")

print(f"true_pos: {true_pos}, true_neg: {true_neg}, false_pos: {false_pos}, false_neg: {false_neg}")

The correct guesses are: 207 and the wrong guesses are: 163.
true_pos: 196, true_neg: 11, false_pos: 1, false_neg: 162
